In [1]:
%load_ext autoreload
%autoreload 2
import os
import os.path
import numpy as np
import sklearn
import sklearn.model_selection
import sklearn.linear_model
import sklearn.ensemble
import spacy
import sys
from sklearn.feature_extraction.text import CountVectorizer
from anchor import anchor_text
import time


2023-05-13 18:38:42.971702: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2023-05-13 18:38:44.052224: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer.so.7'; dlerror: libnvinfer.so.7: cannot open shared object file: No such file or directory; LD_LIBRARY_PATH: /opt/ros/humble/opt/rviz_ogre_vendor/lib:/opt/ros/humble/lib/x86_64-linux-gnu:/opt/ros/humble/lib
2023-05-13 18:38:44.052307: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer_plugin.so.7'; dlerror: libnvinfer_plugin.so.7: cannot open shared object file: No such file or directory; LD_LIBRARY_PATH: /opt/ros/humble/opt/rviz_ogre_ve

In [2]:
# dataset from http://www.cs.cornell.edu/people/pabo/movie-review-data/
# Link: http://www.cs.cornell.edu/people/pabo/movie-review-data/rt-polaritydata.tar.gz
def load_polarity(path='/home/marcotcr/datasets/sentiment-sentences'):
    data = []
    labels = []
    f_names = ['rt-polarity.neg', 'rt-polarity.pos']
    for (l, f) in enumerate(f_names):
        for line in open(os.path.join(path, f), 'rb'):
            try:
                line.decode('utf8')
            except:
                continue
            data.append(line.strip())
            labels.append(l)
    return data, labels

In [3]:
import pandas as pd

# Load CSV file using pandas
data_df = pd.read_csv('/home/rosario/explainable/Bachelor/SebastianCode/datasets/datasets/AG_NEWS/train.csv')

# Extract data and labels
data = data_df.values#tolist()  # Replace 'data_column' with the name of your data column

data_df = data_df[~data_df.isin([3, 4]).any(axis=1)]
y = [sublist[0] for sublist in data_df.values]
X = [sublist[1] for sublist in data_df.values]
print(X)

len(X) 
print(X)


['Phelps, Thorpe Advance in 200 Freestyle (AP)', 'Reds Knock Padres Out of Wild-Card Lead (AP)', 'Dreaming done, NBA stars awaken to harsh Olympic reality (AFP)', 'Indians Beat Twins 7-1, Nearing AL Lead (AP)', 'Galaxy, Crew Play to 0-0 Tie (AP)', 'USC Begins Season Where It Ended, at No. 1 (AP)', "Italy's Pennetta Wins Idea Prokom Open (AP)", 'Tough Race Ahead for Swimmer Phelps', 'Iranian Will Not Meet Israeli in Olympics Due to Weight', 'Tiger Runs Out of Steam After Storming Start', 'Colander Misses Chance to Emulate Jones', 'AL Wrap: Olerud Cheers Yankees by Sinking Ex-Team', 'NL Wrap: Jones Homers Twice as Braves Down Cards', "Olympics-Doping-Greek Media Put Country's Honor Above Athletes", 'Olympics-Rowing-U.S. Eight Beats Canada to Set World Best Time', 'Singh Leads, but Leonard Is Following', 'Olerud Bails Out Loaiza in His Latest Bungled Audition', 'Family circle', 'Notables', 'Cubs get delivery from Wood', 'Leskanic winning arms race', 'Rehabbing his career', 'Warmer and wil

In [4]:
import custionGetTokenizer

tokenizer = custionGetTokenizer.get_tokenizer('basic_english')

nlp = spacy.load('en_core_web_sm')


In [5]:
#data, labels = load_polarity()
train, test, train_labels, test_labels = sklearn.model_selection.train_test_split(X, y, test_size=0.020633333, random_state=42)
print(len(train))
test, val, test_labels, val_labels = sklearn.model_selection.train_test_split(test, test_labels, test_size=.5, random_state=42)
train_labels = np.array(train_labels)
test_labels = np.array(test_labels)
val_labels = np.array(val_labels)

58762


In [6]:
print(len(train))

58762


In [7]:
DATA_ROOT = "/home/rosario/explainable/Bachelor/otherCode/SebastianCode/datasets"

import torch
from torchtext.data.utils import get_tokenizer
from torchtext.vocab import build_vocab_from_iterator
from scipy.sparse import csr_matrix

from datasets import _get_vocab, _build_collate_fn
from torch.nn.utils.rnn import pad_sequence


vocab = _get_vocab(name='AG_NEWS', train_iter = iter(X))
padding_val = vocab['<pad>']
def label_pipeline(input):
    return int(input) - 1


def text_pipeline(input):
    return vocab(tokenizer(input))


def collate_text(batch):
    label_list, text_list, offsets = [], [], [0]
    for (_label, _text) in batch:
        label_list.append(label_pipeline(_label))
    processed_text = torch.tensor(text_pipeline(_text), dtype=torch.int64)
    text_list.append(processed_text)

    #labels = torch.tensor(label_list, dtype=torch.int64)
    text = pad_sequence(text_list, batch_first=True, padding_value=padding_val)
    return text

collate_batch, size_vocab = _build_collate_fn(vocab, label_pipeline)

print(type(collate_batch))
print(size_vocab)

def preprozess(textList):
    tempLsit = []
    for i in textList:
        #print(i)
        #print(tokenizer(i))
        #print(vocab(tokenizer(i)))
        #print()
        tempLsit.append(torch.tensor(vocab(tokenizer(i)), dtype=torch.int64))
    tempLsit = pad_sequence(tempLsit, batch_first=True, padding_value=padding_val)

    return tempLsit

#print(val)
val_vectors = preprozess(val)
test_vectors = preprozess(test)
train_vectors = preprozess(train)
print(test[-1])
print(test_vectors[-1])


looking for vocab in /home/rosario/explainable/Bachelor/otherCode/SebastianCode/datasets/AG_NEWS/vocab.torch
<class 'function'>
58762
Wigley makes clean break from Southampton
tensor([9752,  799, 3471,  979,   31, 2843,    1,    1,    1,    1,    1,    1,
           1,    1,    1,    1,    1,    1,    1,    1,    1,    1,    1,    1])


In [8]:

# need to VEKTORIZE DATA LIKE SEBASITAN BUT WITH DF_DATA 
"""




























#def _get_vocab(name='AG_NEWS', train_iter=None):
#    vocab_path = f"{DATA_ROOT}/{name}/vocab.torch"
#    print(f"looking for vocab in {vocab_path}")
#    try:
#        print("asasWAWAW")
#        vocab = torch.load(vocab_path)
#    except FileNotFoundError:
#        print("asas")
#        print("Vocab not found, building vocab ...")
#        tokenizer = get_tokenizer('basic_english')
#        def yield_tokens(data_iter):
#            for _, text in data_iter:
#                yield tokenizer(text)
#        vocab = build_vocab_from_iterator(yield_tokens(train_iter), specials=['<unk>', '<pad>'])
#        vocab.set_default_index(vocab['<unk>'])
#        torch.save(vocab, vocab_path)
#        print(f"... done, saved vocab of {len(vocab)} words in {vocab_path}")
#    return vocab
#
#vocab = _get_vocab(name='AG_NEWS', train_iter = iter(X))

padding_val = vocab['<pad>']

from torch.nn.utils.rnn import pad_sequence


def text_pipeline(input):
    return vocab(tokenizer(input))


def collate_text(text):
    label_list, text_list, offsets = [], [], [0]
    #for (_label, _text) in batch:
    #    label_list.append(label_pipeline(_label))
    processed_text = torch.tensor(text_pipeline(text), dtype=torch.int64)
    text_list.append(processed_text)

    #labels = torch.tensor(label_list, dtype=torch.int64)
    text = pad_sequence(text_list, batch_first=True, padding_value=padding_val)
    return text

print(train)

from torch import nn

n_classes = 2

size_vocab = len(train)

embedding_dim = 128

embed = nn.Embedding(size_vocab, embedding_dim, sparse=False)

text = train[0] #"Giddy Phelps Touches Gold for First Time Michael Phelps won the gold medal in the 400 individual medley and set a world record in a time of 4 minutes 8.26 seconds."
vekoorized = collate_text(text)
vectorisedList = []

def vectorizeData(data):
    listTemp = []
    for i in data:
        #listTemp.append(embed(collate_text(i)))
        listTemp.append(collate_text(i)[0])
    print(collate_text(i)[0])
    return listTemp




train_vectors =  vectorizeData(train)
test_vectors = vectorizeData(test)
val_vectors = vectorizeData(val)


counter =0
for i in train_vectors:
    counter += 1
    print(np.shape(i))
    print(i)
    if counter > 10:
        break
"""

'\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n#def _get_vocab(name=\'AG_NEWS\', train_iter=None):\n#    vocab_path = f"{DATA_ROOT}/{name}/vocab.torch"\n#    print(f"looking for vocab in {vocab_path}")\n#    try:\n#        print("asasWAWAW")\n#        vocab = torch.load(vocab_path)\n#    except FileNotFoundError:\n#        print("asas")\n#        print("Vocab not found, building vocab ...")\n#        tokenizer = get_tokenizer(\'basic_english\')\n#        def yield_tokens(data_iter):\n#            for _, text in data_iter:\n#                yield tokenizer(text)\n#        vocab = build_vocab_from_iterator(yield_tokens(train_iter), specials=[\'<unk>\', \'<pad>\'])\n#        vocab.set_default_index(vocab[\'<unk>\'])\n#        torch.save(vocab, vocab_path)\n#        print(f"... done, saved vocab of {len(vocab)} words in {vocab_path}")\n#    return vocab\n#\n#vocab = _get_vocab(name=\'AG_NEWS\', train_iter = iter(X))\n\npadding_val = vocab[\'<pad>\']\n\nfrom torch.nn.utils.rnn i

In [9]:
#vectorizer = CountVectorizer(min_df=1)
#vectorizer.fit(train)
from torch import nn

n_classes = 2

size_vocab = len(train)

embedding_dim = 128

#embed = nn.Embedding(size_vocab, embedding_dim, sparse=False)


#a
#NEED to  do custom vectorizer like my model  ?? 
#  

#t#rain_vectors = vectorizer.transform(train)
#print(len(train_vectors.toarray()))#
#test_vectors = vectorizer.transform(test)
#val_vectors = vectorizer.transform(val)
#print(type(test_vectors))
#train_vectors = embed(train_vectors)
#test_vectors = embed(test_vectors)
#val_vectors = embed(val_vectors)

#train_vectors = vectorizer.transform(train)
##print(len(train_vectors.toarray()))
#test_vectors = vectorizer.transform(test)
#val_vectors = vectorizer.transform(val)

In [10]:
#c = sklearn.linear_model.LogisticRegression()
#c.fit(train_vectors, train_labels)

import models
import  nltk
import torch


# Tokenize the sentences into words or tokens
#tokens = [word for sentence in train for word in nltk.word_tokenize(sentence)]

#size_vocab = len(set(tokens))
#print(size_vocab)

c = models.SentenceCNN(n_classes=n_classes, embed_dim=embedding_dim, vocab_size=size_vocab)
#/home/rosario/explainable/Bachelor/otherCode/SebastianCode/Models/finalModel
c.load_state_dict(torch.load("/home/rosario/explainable/Bachelor/otherCode/SebastianCode/Models/finalModel"))

# c = sklearn.ensemble.RandomForestClassifier(n_estimators=500, n_jobs=10)

print(type(val_vectors[0]))

preds = c.predict(np.array(val_vectors))
print("===")
print(preds)
print('Val accuracy', sklearn.metrics.accuracy_score(val_labels, preds))
def predict_lr(texts):
    return c.predict(preprozess(texts))


<class 'torch.Tensor'>
===
[1 1 0 0 0 1 0 0 0 1 0 1 1 1 1 1 1 0 0 0 1 0 0 1 1 1 1 0 0 0 0 0 0 1 1 0 0
 0 0 1 1 1 0 1 0 0 1 1 0 0 0 1 1 1 0 0 1 1 1 0 0 1 1 0 1 0 0 1 0 1 0 0 1 0
 0 0 1 0 1 1 0 1 0 1 1 1 0 1 0 1 0 1 1 0 0 0 1 0 0 0 1 0 1 0 1 1 1 0 1 1 1
 0 0 0 1 0 0 0 1 1 0 0 1 0 0 1 1 1 1 0 0 1 1 1 0 1 1 0 0 1 1 0 1 1 1 0 1 1
 1 1 1 0 1 0 1 1 1 0 1 0 1 1 1 0 1 0 1 0 0 1 1 1 0 1 0 1 0 0 1 0 1 1 1 1 1
 1 0 1 0 0 1 0 0 0 1 0 0 0 1 1 1 1 1 0 1 0 1 0 0 1 1 0 0 1 0 1 0 0 0 1 1 0
 0 0 0 1 0 1 0 1 1 0 1 1 0 0 0 1 1 1 0 0 1 0 0 1 1 1 0 0 0 0 1 0 1 0 1 0 1
 1 1 1 1 0 1 0 1 0 0 0 1 1 0 0 0 0 1 0 0 0 1 0 1 0 1 1 0 0 1 0 0 1 1 0 0 0
 0 0 0 1 0 0 1 1 0 1 1 0 1 0 0 1 1 1 0 1 0 0 0 0 0 1 1 1 1 0 0 0 0 0 0 0 0
 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 1 1 1 1 1 0 0 1 1 1 1 1 1 0 1 1 1
 1 1 1 0 1 1 0 1 0 1 1 0 0 1 0 0 0 0 1 0 1 1 1 0 1 1 0 1 0 0 1 0 0 1 0 0 1
 1 1 1 0 0 1 0 0 0 1 0 1 0 0 1 0 0 1 1 1 1 0 0 1 1 1 1 0 1 0 0 0 1 1 1 1 1
 0 0 0 0 1 1 1 0 0 1 1 1 0 0 1 0 0 1 0 0 0 0 1 0 1 0 0 0 1 0 1 0 0 1 1 1 

In [11]:
#explainer = anchor_text.AnchorText(tokenizer, ['0', '1'], use_unk_distribution=True)
#  needs spacy cause of AttributeError: 'str' object has no attribute 'text'

explainer = anchor_text.AnchorText(nlp, ['tsd', 'assd'], use_unk_distribution=True) # TRUE

In [12]:
np.random.seed(1)
text = 'This is a good book .'
print(predict_lr([text]))
print(explainer.class_names)
pred = explainer.class_names[predict_lr([text])[0]-1]
alternative =  explainer.class_names[1 - predict_lr([text])[0]]
print('Prediction: %s' % pred)
exp = explainer.explain_instance(text, predict_lr, threshold=0.95)


[1]
['tsd', 'assd']
Prediction: tsd


In [13]:
print('Anchor: %s' % (' AND '.join(exp.names())))
print('Precision: %.2f' % exp.precision())
print()
print('Examples where anchor applies and model predicts %s:' % pred)
print()
print('\n'.join([x[0] for x in exp.examples(only_same_prediction=True)]))
print()
print('Examples where anchor applies and model predicts %s:' % alternative)
print()
print('\n'.join([x[0] for x in exp.examples(partial_index=0, only_different_prediction=True)]))


Anchor: book AND a AND good AND . AND This AND is
Precision: 0.84

Examples where anchor applies and model predicts tsd:

This is a good book .
This is a good book .
This is a good book .
This is a good book .
This is a good book .
This is a good book .
This is a good book .
This is a good book .
This is a good book .
This is a good book .

Examples where anchor applies and model predicts tsd:

UNK UNK UNK UNK book UNK
UNK is UNK good book UNK
UNK UNK UNK good book .
This is UNK good book .
UNK UNK a UNK book .
UNK UNK UNK good book UNK
This UNK UNK UNK book .
UNK is UNK good book UNK
UNK UNK UNK UNK book UNK
UNK UNK UNK UNK book .


## Using BERT

The distribution above is a bit naive, and you get a lot of sentences that don't look realistic.  
Let's use BERT to perturb the data:

In [14]:
explainer = anchor_text.AnchorText(nlp, ['negative', 'positive'], use_unk_distribution=False)

/home/rosario/.local/lib/python3.10/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [15]:
np.random.seed(1)
text = 'This is a good book .'
pred = explainer.class_names[predict_lr([text])[0]]
alternative =  explainer.class_names[1 - predict_lr([text])[0]]
print('Prediction: %s' % pred)
b = time.time()
exp = explainer.explain_instance(text, predict_lr, threshold=0.95, verbose=False)
print('Time: %s' % (time.time() - b))

Prediction: positive


/home/rosario/.local/lib/python3.10/site-packages/anchor/anchor_text.py:43: UserWarning: Creating a tensor from a list of numpy.ndarrays is extremely slow. Please consider converting the list to a single numpy.ndarray with numpy.array() before converting to a tensor. (Triggered internally at ../torch/csrc/utils/tensor_new.cpp:245.)
  to_pred = torch.tensor([encoded], device=self.device)


Time: 188.46563577651978


In [16]:
print('Anchor: %s' % (' AND '.join(exp.names())))
print('Precision: %.2f' % exp.precision())
print()
print('Examples where anchor applies and model predicts %s:' % pred)
print()
print('\n'.join([x[0] for x in exp.examples(only_same_prediction=True)]))
print()
print('Examples where anchor applies and model predicts %s:' % alternative)
print()
print('\n'.join([x[0] for x in exp.examples(only_different_prediction=True)]))

Anchor: book AND good AND This AND . AND a
Precision: 0.86

Examples where anchor applies and model predicts positive:

This is a good book .
This is a good book .
This indicates a good book .
This price a good book .
This is a good book .
This is a good book .
This is a good book .
This is a good book .
This is a good book .
This is a good book .

Examples where anchor applies and model predicts negative:

This is a good book .
This is a good book .
This is a good book .
This as a good book .
This is a good book .
This is a good book .
This is a good book .
This is a good book .
This is a good book .
This is a good book .


In [17]:
print('Partial anchor: %s' % (' AND '.join(exp.names(0))))
print('Precision: %.2f' % exp.precision(0))
print()
print('Examples where anchor applies and model predicts %s:' % pred)
print()
print('\n'.join([x[0] for x in exp.examples(partial_index=0, only_same_prediction=True)]))
print()
print('Examples where anchor applies and model predicts %s:' % alternative)
print()
print('\n'.join([x[0] for x in exp.examples(partial_index=0, only_different_prediction=True)]))

Partial anchor: book
Precision: 0.57

Examples where anchor applies and model predicts positive:

paradise is a comic book adaptation
• special commemorative poem book .
here is his first book .
alma is a comic book .
• • a traveling book .
this is a substantial book .
international charity protection charity book 2004
. read a library book .
She is another recent book ;
1987 : west coast book award

Examples where anchor applies and model predicts negative:

this is a reference book .
prize is a picture book !
* is ##rae ^ book ##ward
2019 - global map book winner
t ##um ##ark ##cam book chapters
it is a chess book .
revelation is an intelligent book .
next is soul ##ful book soundtrack
wilderness is a biblical book .
books ##tation > < book >


In [18]:
np.random.seed(1)
text = 'Michal jordan won another championship.'
pred = explainer.class_names[predict_lr([text])[0]]
alternative =  explainer.class_names[1 - predict_lr([text])[0]]
print('Prediction: %s' % pred)
b = time.time()
exp = explainer.explain_instance(text, predict_lr, threshold=0.95, verbose=False, onepass=True)
print('Time: %s' % (time.time() - b))

Prediction: positive
Time: 8.750126838684082


In [19]:
print('Anchor: %s' % (' AND '.join(exp.names())))
print('Precision: %.2f' % exp.precision())
print()
print('Examples where anchor applies and model predicts %s:' % pred)
print()
print('\n'.join([x[0] for x in exp.examples(only_same_prediction=True)]))
print()
print('Examples where anchor applies and model predicts %s:' % alternative)
print()
print('\n'.join([x[0] for x in exp.examples(only_different_prediction=True)]))

Anchor: another AND won
Precision: 1.00

Examples where anchor applies and model predicts positive:

pad ##x won another championships .
each ##amo won another property :
par ##ord won another competition .
ya ##at won another games .
c state won another 60 .
lid team won another replay .
2017 ##ca won another challenge ;
cast ##ay won another £2 .
no ##k won another three :
lava ##wich won another classification .

Examples where anchor applies and model predicts negative:




In [20]:
print('Partial anchor: %s' % (' AND '.join(exp.names(0))))
print('Precision: %.2f' % exp.precision(0))
print()
print('Examples where anchor applies and model predicts %s:' % pred)
print()
print('\n'.join([x[0] for x in exp.examples(partial_index=2, only_same_prediction=True)]))
print()
print('Examples where anchor applies and model predicts %s:' % alternative)
print()
print('\n'.join([x[0] for x in exp.examples(partial_index=2, only_different_prediction=True)]))

Partial anchor: another
Precision: 0.93

Examples where anchor applies and model predicts positive:



IndexError: list index out of range

## See a visualization of the anchor with examples and etc (won't work if you're seeing this on github)

In [ ]:
exp.show_in_notebook()